We'll work on a dataset `gro.csv` for **credit scoring** that was proposed some years ago as a data challenge on some [data challenge website](https://www.kaggle.com).

It is a realistic and *messy* dataset with a lot of missing values, several types (date, categorical, numeric) of *features*, so that serious data cleaning and formating is required.

This dataset contains the following columns:

| Column name          | Description |
|:---------------------|:------------|
| `BirthDate`            | Date of birth of the client |
| `Customer_Open_Date`   | Creation date of the client's first account at the bank |
| `Customer_Type`        | Type of client (existing / new) | 
| `Educational_Level`    | Highest diploma |
| `Id_Customer`          | Id of the client |
| `Marital_Status`       | Family situation |
| `Nb_Of_Products`       | Number of products held by the client |
| `Net_Annual_Income`    | Annual revenue |
| `Number_Of_Dependant`  | Number of dependents |
| `P_Client`             | Non-disclosed feature |
| `Prod_Category`        | Product category |
| `Prod_Closed_Date`     | Closing date of the last product |
| `Prod_Decision_Date`   | Decision date of the last agreement for a financing product |
| `Prod_Sub_Category`    | Sub-category of the product |
| `Source`               | Financing source (Branch or Sales) |
| `Type_Of_Residence`    | Residential situation |
| `Y`                    | Credit was granted (yes / no) |
| `Years_At_Business`    | Number of year at the current job position |
| `Years_At_Residence`   | Number of year at the current housing |

# Your job

Read and explore the `gro.csv` dataset using `pandas`, `matplotlib`,  `seaborn`, and `plotly`.

{{< fa hand-point-right >}}

- The column separator in the CSV file is not `,` but `;` so you need to use the `sep` option in `pd.read_csv`
- The categorical columns must be imported as `category` type  (not `object`)
- Something weird is going on with the `Net_Annual_Income` column... Try to  understand what is going on and try to fix it 
- Several columns are empty, we need to remove them (or not even read them)
- Dates must be imported as dates and not strings
- Remove rows with missing values

Many of these things can be done right at the beginning, when reading the CSV file, through some options to the `pd.read_csv()` function. You might need to read carefully its documentation in order to see which options are useful. Once you are happy with your importation and cleaning of the data, you can:
- Use `pandas`  and some *graphical backend* to perform data visualization ...
- ... in order to understand visually the impact of some features on `Y` (credit was granted or not). For this, you need to decide which plots make sense for this and produce them

We will provide thorough explanations and code that performs all of this in subsequent sessions.


# A quick and dirty import

Let's import the data into a pandas dataframe, as simply as possible
The only thing we care about for now is the fact that the column separator 
is `';'` and not `','` (American `csv` files use `,` as a default separator, Continental European `csv` files use `;`). 

In [ ]:
import requests
import os

# The path containing your notebook
path_data = './'
# The name of the file
filename = 'gro.csv.gz'
# the file path
fpath = os.path.join(path_data, filename)

if os.path.exists(fpath):
    print(f'The file "{fpath}" already exists.')
else:
    url = 'https://stephane-v-boucheron.fr/data/gro.csv.gz'
    r = requests.get(url)
    with open(fpath, 'wb') as f:
        f.write(r.content)
    print(f'Downloaded file "{fpath}".')

In [ ]:
import numpy as np
import pandas as pd
import plotly.express as px
import matplotlib.pyplot as plt
import seaborn as sns
from pandas import Timestamp
import pickle as pkl

In [ ]:
filename = "gro.csv.gz"
df = pd.read_csv(filename, sep=';')
df.head(n=5)

In [ ]:
df.columns

**Remark**. There are weird columns at the right end, they look empty. 
They are not mentioned in the data description (metadata).

In [ ]:
df.info()

In [ ]:
df["BirthDate"].head()

In [ ]:
type(df.loc[0, 'BirthDate'])

This means that dates are indeed imported as a strings...

In [ ]:
df['Prod_Sub_Category'].head()

In [ ]:
type(df.loc[0, 'Prod_Sub_Category'])

Categorical variables are imported as a strings as well

In [ ]:
df['Net_Annual_Income'].head(n=10)

In [ ]:
type(df.loc[0, 'Net_Annual_Income'])

Net actual income is a string as well ! While it is clearly a number !!!

In [ ]:
df.describe(include='all')

{{< fa hand-point-right >}}  Method `describe()` delivers a summary for numerical columns. It provides location parameters (mean and median) and scale parameters (standard deviation and Inter Quartile Range (IQR)). For other types of columns it is useless.  

In [ ]:
df_description = df.describe(include='all')

df_description.index

## Checkup 

We have to improve data  import.

Here is a list of the problems we face.

- The last three columns are empty
- Dates are encoded as `str` (Python `string` type)
- There are  many missing values
- Categorical features are encoded are `str`
- The `Net_Annual_Income` is imported as a string

By looking at column names, column descriptions, and common sense, we can infer the type of features we face.
There are dates features, numerical features, and categorical features.
Some features can be either treated as categorical or numerical.

- There are **many** missing values, that need to be handled.
- The annual net income is imported as a string,  why?
- Dates should be handled as  dates and not as strings: this allows us to use the date and time processing functions from the [`datetime` package](https://docs.python.org/3/library/datetime.html).

Here is a tentative structure of the features

**Numerical features**

- `Years_At_Residence`
- `Net_Annual_Income`
- `Years_At_Business`

**Features to be decided**

- `Number_Of_Dependant`
- `Nb_Of_Products`

**Categorical features**

- `Customer_Type`
- `P_Client`
- `Educational_Level`
- `Marital_Status`
- `Prod_Sub_Category`
- `Source`
- `Type_Of_Residence`
- `Prod_Category`

**Date features**

- `BirthDate`
- `Customer_Open_Date`
- `Prod_Decision_Date`
- `Prod_Closed_Date`

# A closer look at the import problems

Let us find solutions to all these import problems.

## The last three columns are  empty 

It seems to come from the fact that the data always ends with several `';'` characters. 
We can remove them simply using the `usecols` option from `read_csv`.


> Passing how="all" to method `dropna()` (`df.dropna(how="all")`) will drop only rows that are all NA:

In [ ]:
# all([True, False, True])
# df.isna().map(all)

df.dropna(how="all").info()

## Dates are actually `str`

We need to specify which columns must be encoded as dates using the `parse_dates` option from `read_csv`.
Fortunately enough, `pandas` is clever enough to interpret the date format.

In [ ]:
type(df.loc[0, 'BirthDate'])

## There is a lot of missing values 

We will see below that a single column contains most missing values.

In [ ]:
df.isnull().sum()

In [ ]:
'01/01/1985'

The column `Prod_Closed_Date` contains mostly missing values !

In [ ]:
df[['Prod_Closed_Date']].head(5)

Remove the useless columns and check the remaining missing values

In [ ]:
df.drop(['Prod_Closed_Date', 
         'Unnamed: 19', 
         'Unnamed: 20', 
         'Unnamed: 21'], 
         axis="columns", 
         inplace=True)

In [ ]:
df.head()

Let's display the rows with missing values and let's highlight them

In [ ]:
df[df.isnull().any(axis="columns")]\
  .style\
  .highlight_null()

## Categorial features are `str`

We need to say the dtype we want to use for some columns using the `dtype` option of `read_csv`.

In [ ]:
type(df.loc[0, 'Prod_Sub_Category'])

In [ ]:
df['Prod_Sub_Category'].unique()

## The annual net income is imported as a string

This problem comes from the fact that the decimal separator is in continental European notation: it's a `','` and not a `'.'`, so we need to specify it using the `decimal` option to `read_csv`.  

In [ ]:
type(df.loc[0, 'Net_Annual_Income'])

In [ ]:
df['Net_Annual_Income'].head(n=10)

# A better import of the data

- We build a `dict` that specifies the `dtype` to use for each column 
and pass it to `read_csv()` using the `dtype` option
- We also specify the `decimal`, `usecols` and `parse_dates` options

::: {.callout-note}

Some columns could be imported as `int`. 

However, `pandas` is built above `numpy`, `pandas` does not support columns  with integer `dtype` and missing values.

:::

As columnn type inference does not work universally, a safeguard consists in providing `read_csv()` with optinal argument `dtype`. The default value is `None`. The default value is overriden by a dictionary where keys are strings denoting the column names where type inference is not satisfactory and values denote the desired types. 

In [ ]:
gro_dtypes = {
    'Years_At_Residence': np.int64,
    'Net_Annual_Income' : np.float64,
    'Years_At_Business': np.float64,
    'Number_Of_Dependant': np.float64,
    'Nb_Of_Products': np.int64,
    'Customer_Type': 'category',
    'P_Client': 'category',
    'Educational_Level': 'category',
    'Marital_Status': 'category',
    'Prod_Sub_Category': 'category',
    'Source': 'category',
    'Type_Of_Residence': 'category',
    'Prod_Category': 'category',
}

::: {.callout-note}

Note that the intended type is `'category'`, the function still has to infer the categories from the data, and to build the actual categorical type with a proper encoding. 

:::

We can use the *dictionary unpacking* capabilities of Python to save the overriden 
keyword parameters into a dictionary. The dictionary can be serialized and saved on disc.
It is then considered as metadat. 

In [ ]:
gro_read_spec_dict = {
    'sep': ';',      # continental separator
    'decimal': ',',  # continental decimal separator
    'usecols': range(19),  # Range of the columns to keep (remove the last three ones)
    'parse_dates': ['BirthDate', # Which columns should be parsed as dates ?
                    'Customer_Open_Date', 
                    'Prod_Decision_Date', 
                    'Prod_Closed_Date'],
    'dtype': gro_dtypes  # Specify some dtypes
  }

Using the metadata packed into the dictionary turns easy and concise. The same metadata can be reused 
for any `csv` file with the same features.

In [ ]:
df = pd.read_csv(
    "gro.csv.gz",      # Filename
    ** gro_read_spec_dict
)

In [ ]:
df.info()

::: {.callout-note}

Column `BirthDate` is meant to be a `date` column. Nevertheless, is is not converted 
to a `date` or `datetime` column. 

> If a column or index cannot be represented as an array of `datetime`, say because of an unparsable value or a mixture of timezones, the column or index will be returned unaltered as an `object` data type. For non-standard `datetime` parsing, use `to_datetime()` after `read_csv()`.


:::

If we do not set optional arguments, `pd.to_datetime()` fails to convert `df['BirthDate']`.

In [ ]:
#| eval: false
bd = pd.to_datetime(df['BirthDate'])

We get a message:

> ValueError: time data "13/06/1974" doesn't match format "%m/%d/%Y", at position 2. You might want to try:
    - passing `format` if your strings have a consistent format;
    - passing `format='ISO8601'` if your strings are all ISO8601 but not necessarily in exactly the same format;
    - passing `format='mixed'`, and the format will be inferred for each element individually. You might want to use `dayfirst` alongside this.

Indeed,  the format of the first items in column `BirthDate` seems to be `%d/%m/%Y` (as for the other date columns).

An easy fix consists in setting optional argument `dayfirst` to `True`. 

In [ ]:
egg = pd.to_datetime(df['BirthDate'], dayfirst=True)

A possibly safer 

In [ ]:
spam = pd.to_datetime(df['BirthDate'], format='%d/%m/%Y')

In [ ]:
np.all(spam==egg)

We can improve our import by enriching our dictionary of optional arguments. 

In [ ]:
gro_read_spec_dict['date_format']= '%d/%m/%Y' 

In [ ]:
df = pd.read_csv(
    "gro.csv.gz",      # Filename
    ** gro_read_spec_dict
)

In [ ]:
df.info()

In [ ]:
df['Prod_Sub_Category'].head()

In [ ]:
type(df.loc[0, 'BirthDate'])

Let us  remove `Prod_Closed_Date` (mostly contains missing values)

In [ ]:
prod_closed_date = df.pop('Prod_Closed_Date')
df.shape

In [ ]:
df.info()

And remove the remaining rows with missing values

In [ ]:
print(df.shape)
df = df.dropna()
print(df.shape)

In [ ]:
# Now we save the cleaned dataset into a CSV file
df.to_csv("gro_cleaned.csv")

In [ ]:
!ls -al gro_*

::: {.callout-note}

Read  the [Data loading section in the Pandas book](https://wesmckinney.com/book/accessing-data)

We used the following subsections:

- Type inference and data conversion
- Date and time parsing
- Unclean data issues

[`pandas.read_csv()` has around 50 optional/keywords parameters](https://pandas.pydata.org/docs/reference/api/pandas.read_csv.html). 

:::

In [ ]:
cleaned_spec_dict = {
    'parse_dates': ['BirthDate', 
                    'Customer_Open_Date', 
                    'Prod_Decision_Date'],
    'dtype': gro_dtypes  
}

df = pd.read_csv("gro_cleaned.csv", 
    **cleaned_spec_dict)

df.info()

## Comment on file formats

You can use other methods starting with `.to_XX` to save in another format.

- OK to use `csv` for "small" datasets (several MB). But this is not a self-documented format. 
- Use `pickle` for more compressed and faster format (limited to 4GB). It's the standard binary *serialization* format of `Python`
- `feather` is another fast and lightweight file format for storing data frames. A very popular exchange format. 
- `parquet` is a format for big distributed data (works nicely with `Spark`)

among several others...

::: {.callout-note}

Have a look at the [`PyArrow` package](https://arrow.apache.org/docs/python/)

:::


In [ ]:
df.index

In [ ]:
df.to_pickle("gro_cleaned.pkl")
df.to_parquet("gro_cleaned.parquet")
df.reset_index().to_feather("gro_cleaned.feather")

In [ ]:
df.index

And you can read again using the corresponding `read_XX` function

In [ ]:
df = pd.read_pickle("gro_cleaned.pkl")
df.info()

In [ ]:
!ls -alh gro_cleaned*

## The net income columns is very weird

In [ ]:
income = df['Net_Annual_Income']
income.describe()

In [ ]:
(income <= 100).sum(), (income > 100).sum()

Most values are smaller than 100, while some are much much larger...

In [ ]:
%matplotlib inline

sns.set_context("notebook", font_scale=1.2)

In [ ]:
sns.displot(x='Net_Annual_Income', 
            data=df, 
            bins=20,
            height=4, 
            aspect=1.5)

This is annoying, we don't really see much...

In [ ]:
sns.displot(x='Net_Annual_Income', 
            data=df, 
            bins=20, 
            height=4, 
            aspect=1.5, 
            log_scale=(False, True))

Distribution for less than 100K revenue

In [ ]:
sns.displot(x='Net_Annual_Income', 
            data=df[df['Net_Annual_Income'] < 100], 
            bins=15, 
            height=4, 
            aspect=1.5)

Distribution for less than 400K revenue

In [ ]:
sns.displot(x='Net_Annual_Income',
            data=df[df['Net_Annual_Income'] < 400], 
            bins=15, 
            height=4, 
            aspect=1.5)

In [ ]:
(df['Net_Annual_Income'] == 36.0).sum()

In [ ]:
income_counts = (
    pd.DataFrame({
        "income_category": df['Net_Annual_Income'].astype("category"),
        "income": df['Net_Annual_Income']
    })
    .groupby("income_category")
    .count()
    .reset_index()
    .rename(columns={"income": "#customers"})
    .sort_values(by="#customers", 
                 axis="index", 
                 ascending=False)
)

income_counts["%cummulative clients"] \
    = income_counts["#customers"].cumsum() / income_counts["#customers"].sum()

( 
    income_counts
        .iloc[:20]
        .style.bar(subset=["%cummulative clients"],         vmin=0, vmax=1)
)

- We have some overrepresented values (many possible explanations for this)
- To clean the data, we can, for instance, keep only the revenues between [10, 200], or leave it as such

In [ ]:
df = df[(df['Net_Annual_Income'] >= 10) & (df['Net_Annual_Income'] <= 200)]

sns.displot(x='Net_Annual_Income', data=df, bins=15, height=4, aspect=1.5)

# Some data visualization with `pandas` + `seaborn`

In [ ]:
plt.figure(figsize=(8, 5))

sns.stripplot(x='Educational_Level', 
              y='Net_Annual_Income', 
              hue='Y', 
              jitter=True, 
              data=df)

In [ ]:
plt.figure(figsize=(12, 6))
sns.boxplot(x='Educational_Level', y='Net_Annual_Income', 
            hue='Y', data=df)

In [ ]:
plt.figure(figsize=(12, 6))

sns.violinplot(x='Marital_Status', y='Net_Annual_Income', 
               hue='Y', split=True, data=df)

In [ ]:
plt.figure(figsize=(10, 5))

sns.countplot(x='Marital_Status', hue='Y', data=df)

In [ ]:
fig, axes = plt.subplots(nrows=4, ncols=3, figsize=(16, 16))

columns = ['Customer_Type', 'P_Client', 'Educational_Level', 
           'Number_Of_Dependant', 'Marital_Status', 'Prod_Sub_Category',
           'Source', 'Type_Of_Residence', 'Nb_Of_Products', 
           'Prod_Category', 'Y']

for i, colname in enumerate(columns):
    sns.countplot(x=colname, data=df, ax=fig.axes[i])


plt.tight_layout()

# Final preparation of the dataset

In [ ]:
# First we make lists of continuous, categorial and date features

cnt_featnames = [
    'Years_At_Residence',
    'Net_Annual_Income',
    'Years_At_Business',
    'Number_Of_Dependant'
]

cat_featnames = [
    'Customer_Type',
    'P_Client',
    'Educational_Level',
    'Marital_Status',
    'Prod_Sub_Category',
    'Source',
    'Type_Of_Residence',
    'Prod_Category',
    'Nb_Of_Products'
]

date_featnames = [
    'BirthDate',
    'Customer_Open_Date',
    'Prod_Decision_Date'
    #'Prod_Closed_Date'
]

## Creation of the features matrix

In [ ]:
df[cnt_featnames].head()

In [ ]:
bin_features = pd.get_dummies(df[cat_featnames],
                              prefix_sep='#', 
                              drop_first=True)

In [ ]:
bin_features.head()

In [ ]:
cnt_features = df[cnt_featnames]
cnt_features.head()

In [ ]:
def age(x):
    today = Timestamp.today()
    return (today - x).dt.days

date_features = df[date_featnames].apply(age, axis="index")

date_features.head()

In [ ]:
today = Timestamp.today()
today

In [ ]:
tt = (today - df["BirthDate"]).loc[0]

In [ ]:
(today - df["BirthDate"]).dt.days

In [ ]:
tt

## Final features matrix

In [ ]:
all_features = pd.concat([bin_features, cnt_features, date_features], axis=1)

In [ ]:
all_features.columns

In [ ]:
all_features.head()

In [ ]:
df_debile = pd.DataFrame({"nom etudiant": ["yiyang", "jaouad", "mokhtar", "massil", "simon"], 
              "portable": [True, True, None, True, False]})

In [ ]:
df_debile

In [ ]:
df_debile.index

In [ ]:
df_debile.dropna().index

In [ ]:
df_debile.info()

::: {.callout-note}

We removed rows that contained missing values. The index of the dataframe is therefore not contiguous anymore

:::


In [ ]:
all_features.index.max()

This could be a problem for later. So let's reset the index to get a contiguous one

In [ ]:
all_features.shape

In [ ]:
all_features.reset_index(inplace=True, drop=True)

::: {.callout-note}

Why does the index matter? 

For example, when adding a new column to a dataframe, only items from the new series that have a corresponding index in the Dataframe will be added. The receiving dataframe is not extended to accomodate the new series.  

:::

In [ ]:
all_features.head()

## Let's save the data using `pickle`

In [ ]:
X = all_features
y = df['Y']

# Let's put eveything in a dictionary
df_pkl = {}
# The features and the labels
df_pkl['features'] = X
df_pkl['labels'] = y
# And also the list of columns we built above
df_pkl['cnt_featnames'] = cnt_featnames
df_pkl['cat_featnames'] = cat_featnames
df_pkl['date_featnames'] = date_featnames

with open("gro_training.pkl", 'wb') as f:
    pkl.dump(df_pkl, f)

In [ ]:
!ls -al gro*

The preprocessed data is saved in a pickle file called `gro_training.pkl`.

# Misc: Graphics with `plotly`

[Pandas Plotly backend](https://plotly.com/python/pandas-backend/)

[Plotly express box](https://plotly.github.io/plotly.py-docs/generated/plotly.express.box.html)

In [ ]:
fig = px.box(df, 
             x='Marital_Status', 
             y='Net_Annual_Income',
             color='Y')

fig.show()

In [ ]:
s = df['Marital_Status'].value_counts()

df_counts = pd.DataFrame({
    'status': s.index.to_list(),
    'count': s.to_list()}
)

In [ ]:
fig = px.bar(df_counts, 
    x="status", 
    y="count", 
    title="Marital Status")

fig.show()